<a href="https://colab.research.google.com/github/Gijslake/DDWT19/blob/master/skills_classificatie/model_tests/vacature_teksten_third_level.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Macroschaal Statistieken

# Belangrijke info:

Dit programma gaat ervan uit dat de volgende bestanden in de drive staan:


*   O'NET database in SQL: /Onet/data/onet_dump2.sql
*   ESCO database in SQL: /ESCO/database/esco-dump.sql
*   Resultaten in CSV: /Osso data/test data/macro_scale_results_1000_vac.csv

Je kan gewoon naar beneden scrollen en de tabellen bekijken. Om ze opnieuw te laden kan alles in één keer gedraaid worden :).

Onderaan worden 9 beroepen getoetst. De gekozen beroepen zijn:
*   1349 "Leidinggevende functies op het gebied van professionele diensten, niet elders geclassificeerd"
*   2431 "Specialisten op het gebied van reclame en marketing"
*   3115 "Technici op het gebied van de werktuigbouwkunde"
*   4222 "Callcentermedewerkers, inkomende berichten"
*   5414 "Beveiligingspersoneel"
*   6113 "Tuinders en kwekers"
*   7233 "Monteurs industriële en landbouwmachines"
*   8332 "Vrachtwagenchauffeurs"
*   9112 "Schoonmakers in hotels, kantoren e.d."

## Milvus server inladen en starten

### Drive Mounten

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


### Pip installaties

In [ ]:
!pip install pandas
!pip install pyyaml
!pip install python-swiftclient python-keystoneclient
!pip install beautifulsoup4
!pip install matplotlib
!pip install seaborn
!pip install mysql-connector-python

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.9/88.9 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 397.9/397.9 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 323.1/323.1 kB 11.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 128.6/128.6 kB 9.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.8/46.8 kB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.1/101.1 kB 10.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 107.5/107.5 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 7.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 16.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 341.8/341.8 kB 21.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for netifaces: filename=netifaces-0.11.0-cp310-cp310-linux_x86_64.whl size=35006 sha256=787c55c29b1a11b1f5c41e9604b06b48a3243aa7f

## MariaDB inladen

### Installeer MariaDB en expect

In [ ]:
# Install MariaDB and expect
!sudo apt-get upgrade
!apt-get install mariadb-server
!apt-get install expect -y

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
Calculating upgrade... Done
The following packages have been kept back:
  libcudnn8 libcudnn8-dev libnccl-dev libnccl2
The following packages will be upgraded:
  base-files binutils binutils-common binutils-x86-64-linux-gnu cuda-keyring
  cuda-toolkit-config-common libbinutils libc-bin libcap2 libctf-nobfd0
  libctf0 libldap-2.5-0 libudev1 linux-libc-dev openssl
15 upgraded, 0 newly installed, 0 to remove and 4 not upgraded.
Need to get 7,022 kB of archives.
After this operation, 69.6 kB of additional disk space will be used.
Get:1 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  cuda-keyring 1.1-1 [4,332 B]
Get:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  cuda-toolkit-config-common 12.3.52-1 [16.4 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 base-files amd64 12ubuntu4.4 [62.6 kB]
Get:4 http://archive.ubuntu.

### ESCO + O'Net database laden

In [ ]:
# Start mariadb service
!sudo service mariadb start &

 * Starting MariaDB database server mariadbd
   ...done.


In [ ]:
# Create admin user
!mysql -u root < ./drive/MyDrive/MariaDB/create_user.sql

In [ ]:
# Run expect script om MariaDB op te zetten samen
!chmod +x ./drive/MyDrive/Onet/mariadb_setup.sh
!./drive/MyDrive/Onet/mariadb_setup.sh

# Laad databases in mariadb
!mysql -u root < ./drive/MyDrive/Onet/data/onet_dump2.sql
!mysql -u root < ./drive/MyDrive/ESCO/database/esco-dump.sql



NOTE: RUNNING ALL PARTS OF THIS SCRIPT IS RECOMMENDED FOR ALL MariaDB
      SERVERS IN PRODUCTION USE!  PLEASE READ EACH STEP CAREFULLY!

In order to log into MariaDB to secure it, we'll need the current
password for the root user. If you've just installed MariaDB, and
haven't set the root password yet, you should just press enter here.

Enter current password for root (enter for none): 
OK, successfully used password, moving on...

Setting the root password or using the unix_socket ensures that nobody
can log into the MariaDB root user without the proper authorisation.

You already have your root account protected, so you can safely answer 'n'.

Switch to unix_socket authentication [Y/n] n
 ... skipping.

You already have your root account protected, so you can safely answer 'n'.

Change the root password? [Y/n] n
 ... skipping.

By default, a MariaDB installation has an anonymous user, allowing anyone
to log into MariaDB without having to have a user account created for
them.  This

### Connectie maken met MariaDB

In [ ]:
import mysql.connector as mariadb

# Connect to local ONET DB
conn_mariadb = mariadb.connect(
        user="admin",
        password="admin",
        host="localhost",
        port=3306
    )

# Cursor aanmaken
cur = conn_mariadb.cursor()

# Data ophalen en verwerken

## Functies voor skills ophalen

In [ ]:
# Haalt lijst met alle URIs op van alle third level skills
def get_third_level_skills():
  # Reset cursor zodat er geen errors zijn
  cur.reset()

  # Voert query uit waarbij alle URIs opgehaald worden voor level 3, hier
  # kunnen eventueel extra velden aan toegevoegd worden indien die nodig
  # zijn (zoals description of labels)
  cur.execute(f"""SELECT DISTINCT esco.skills.uri
  FROM esco.skills
  INNER JOIN esco.hierarchical_relations ON esco.skills.uri=esco.hierarchical_relations.uri_level3
  """)

  # Haal alle results op
  results = cur.fetchall()

  # Return lijst in goede format
  return [result[0] for result in results]

# Haalt recursief van bottom up alle related third level skills op
def get_third_level_skill_from_uri(uri, third_level_skills):
  # Zet ' om URI heen voor query
  uri = "'" + uri.strip() + "'"

  # Verzamelt resultaten
  results_list = []

  # Reset cursor zodat er geen errors zijn
  cur.reset()

  # Voert query uit waarbij de alle bredere URIs opgehaald worden
  cur.execute(f"""SELECT DISTINCT esco.skills.uri, esco.skills.preferred_label, esco.skills.alt_labels, esco.skills.hidden_labels, esco.skills.description
  FROM esco.skills
  INNER JOIN esco.broader_skill_relations ON esco.skills.uri=esco.broader_skill_relations.broader_uri
  AND esco.broader_skill_relations.original_uri = {uri}
  """)

  # Haalt alle resultaten op
  results = cur.fetchall()

  # Itereer over results (Dit werkt ook met 0 of 1 result)
  for result in results:
    # Als deze skill in de third_level_skills lijst staat kan hij worden toegevoegd
    if result[0] in third_level_skills:
      results_list.append(result)

    # Voeg eventueel een resultaat in een diepere iteratie van deze functie toe
    results_list.extend(get_third_level_skill_from_uri(result[0], third_level_skills))

  return results_list

## Algemene data

### Laden uit bestand

In [ ]:
import pandas as pd

# Moet aanwezig zijn voordat blokje gedraaid wordt
csv_path = "/content/drive/MyDrive/Osso data/test data/macro_scale_results_1000_vac.csv"
results_df = pd.read_csv(filepath_or_buffer = csv_path)
results_df = results_df.where(results_df['Source'] == 'esco_db').dropna()
results_df

Skill_id   Source  \
6      http://data.europa.eu/esco/skill/b569f765-86f6...  esco_db   
7      http://data.europa.eu/esco/skill/d81a22a2-4f57...  esco_db   
8      http://data.europa.eu/esco/skill/2c108d0d-c489...  esco_db   
12     http://data.europa.eu/esco/skill/e6ac75a5-1945...  esco_db   
13     http://data.europa.eu/esco/skill/a0ccc96f-edec...  esco_db   
...                                                  ...      ...   
13152  http://data.europa.eu/esco/skill/5ec0bddd-3502...  esco_db   
13153            http://data.europa.eu/esco/isced-f/0821  esco_db   
13154             http://data.europa.eu/esco/isced-f/082  esco_db   
13155  http://data.europa.eu/esco/skill/78e89833-f27e...  esco_db   
13156            http://data.europa.eu/esco/isced-f/0812  esco_db   

                                                    Text  Count  
6      neurologische aandoeningen behandelen\nneurolo...    1.0  
7      deelnemen aan fysiotherapeutisch onderzoek\nVe...    1.0  
8      prenatale zorg bieden\nDe normale progressie v...    1.0  
12     kwaliteit van gravures bepalen\nKwaliteitscont...    2.0  
13     gesproken Spaans begrijpen\ngesproken Spaans v...    1.0  
...                                                  ...    ...  
13152  toezien op onderhoudswerk\nToezien op landscha...    6.0  
13153                                            bosbouw  241.0  
13154                                            bosbouw  275.0  
13155  deelnemen aan het onderhoud van wijnstokken\nd...    9.0  
13156                                           tuinbouw   49.0  

[5494 rows x 4 columns]

### DataFrame invullen en maken voor algemeen

In [ ]:
# Simpele functie die iets toevoegd aan een dictionary
# of een entry aanmaakt als die er nog niet is
def add_to_dict(uri, count, desc, results_dict):

  if uri in results_dict.keys():
    results_dict[uri]['Count'] += count
  else:
    results_dict[uri] = {'Count': count, "Text": desc}

  return results_dict

# Maak lege dictionary
results_dict = {}

# Haal third level skills op
third_level_skills = get_third_level_skills()

# Itereer over algemene database
for index, row in results_df.iterrows():

  # Als de skills niet zelf een third level skill is
  if row['Skill_id'] not in third_level_skills:
    # Zoek third_level skills
    results = get_third_level_skill_from_uri(row['Skill_id'], third_level_skills)

    # Als er resultaten zijn voeg ze toe aan de dictionary
    if results:
      for result in results:
        results_dict = add_to_dict(result[0], row["Count"], "\n".join(part for part in result[1:] if part), results_dict)

  # Anders kunnen we hem direct toevoegen
  else:
    results_dict = add_to_dict(row["Skill_id"], row["Count"], row["Text"], results_dict)

In [ ]:
# Tijdelijke lijst voor resultaten
tmp_list = []

# Maak resultaten interpreteerbaar voor Pandas DataFrame
for item in results_dict.items():
  tmp_list.append({"Skill_id": item[0], "Text": item[1]["Text"], "Count": int(item[1]["Count"])})

# Maak DataFrame
third_level_df = pd.DataFrame(tmp_list)

# Voeg probabilty toe
total_amt = third_level_df["Count"].sum()
third_level_df["Probability"] = third_level_df["Count"] / total_amt

third_level_df

Skill_id  \
0    http://data.europa.eu/esco/skill/73e602a0-f80f...   
1    http://data.europa.eu/esco/skill/7eafec38-621a...   
2    http://data.europa.eu/esco/skill/b88bddd4-210e...   
3    http://data.europa.eu/esco/skill/0b3930a2-8a13...   
4    http://data.europa.eu/esco/skill/a7956044-f468...   
..                                                 ...   
410  http://data.europa.eu/esco/skill/4feed491-dc09...   
411  http://data.europa.eu/esco/skill/a5524d0d-38e5...   
412            http://data.europa.eu/esco/isced-f/0011   
413            http://data.europa.eu/esco/isced-f/0922   
414            http://data.europa.eu/esco/isced-f/0112   

                                                  Text  Count  Probability  
0    verstrekken van medische, tandheelkundige en v...    262     0.003073  
1         wetenschappelijk of marktonderzoek uitvoeren    676     0.007928  
2    voorschrijven en bestellen van medische tests,...     13     0.000152  
3                    de kwaliteit van goederen bewaken    145     0.001701  
4    bedienen van snij-, slijp- en afvlakkingsmachines     64     0.000751  
..                                                 ...    ...          ...  
410                             oplossen van problemen     46     0.000540  
411                  bedienen van mobiele installaties     55     0.000645  
412                   basisonderwijs en -kwalificaties    272     0.003190  
413                      kinderverzorging en jeugdzorg    536     0.006286  
414  opleiding voor leerkrachten in het kleuteronde...    301     0.003530  

[415 rows x 4 columns]

## Data per beroep

### Inladen van dataset

In [ ]:
df_dict = {}

def custom_agg(series):
    return {
        'Count': series.count(),
        'Max_score': series.max(),
        'Avg_score': series.mean()
    }

for ISCO_code in ["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"]:
  tmp_results_df = pd.DataFrame({'Skill_id', 'Source', 'Count', 'Score'})
  data_df = pd.read_csv(f'/content/drive/MyDrive/Osso data/results/results per beroep/{ISCO_code}_results.csv')
  total_skills_amt = len(data_df.index)
  # Group by 'Skill_id' and apply the custom aggregation function
  result = data_df.groupby(['Skill_id', 'Skill_text'])['Score'].agg(custom_agg).reset_index()

  # Use the map function to extract 'Count' and 'Max_Score' into separate columns
  result['Count'] = result['Score'].map(lambda x: x['Count'])
  result['Max_score'] = result['Score'].map(lambda x: x['Max_score'])
  result['Avg_score'] = result['Score'].map(lambda x: x['Avg_score'])
  result['Probability'] = result['Count'].map(lambda x: x / total_skills_amt)

  # Drop the original 'Score' column
  result.drop('Score', axis=1, inplace=True)

  df_dict[ISCO_code] = result

### DataFrame invullen en maken per beroep

In [ ]:
third_level_df_dict = {}

# Haal third level skills op
third_level_skills = get_third_level_skills()

for ISCO_code in ["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"]:
  # Maak lege dictionary
  results_dict = {}

  # Itereer over algemene database
  for index, row in df_dict[ISCO_code].iterrows():

    # Als de skills niet zelf een third level skill is
    if row['Skill_id'] not in third_level_skills:
      # Zoek third_level skills
      results = get_third_level_skill_from_uri(row['Skill_id'], third_level_skills)

      # Als er resultaten zijn voeg ze toe aan de dictionary
      if results:
        for result in results:
          results_dict = add_to_dict(result[0], row["Count"], "\n".join(part for part in result[1:] if part), results_dict)

    # Anders kunnen we hem direct toevoegen
    else:
      results_dict = add_to_dict(row["Skill_id"], row["Count"], row["Skill_text"], results_dict)

  # Tijdelijke lijst voor resultaten
  tmp_list = []

  # Maak resultaten interpreteerbaar voor Pandas DataFrame
  for item in results_dict.items():
    tmp_list.append({"Skill_id": item[0], "Text": item[1]["Text"], "Count": int(item[1]["Count"])})

  # Maak DataFrame
  third_level_df_dict[ISCO_code] = pd.DataFrame(tmp_list)

  # Voeg probabilty toe
  total_amt = third_level_df_dict[ISCO_code]["Count"].sum()
  third_level_df_dict[ISCO_code]["Probability"] = third_level_df_dict[ISCO_code]["Count"] / total_amt

In [ ]:
from google.colab import widgets
from google.colab import data_table

# Maak tabs voor sources
tb = widgets.TabBar(["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"])

for tab in tb.tab_names:
  with tb.output_to(tab, select=(0)):
    display(data_table.DataTable(third_level_df_dict[tab], include_index=False, num_rows_per_page=10))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Statistieken berekenen

In [ ]:
from google.colab import widgets
from google.colab import data_table

def Calculate_metrics(data_specific, data_all):
  data_specific.rename(columns={'Skill_text': 'Text'}, inplace=True)
  merged_df = data_specific.merge(data_all, how='left', on=['Skill_id', 'Text'], suffixes=('_specific', '_all'))
  merged_df['Count_all'].fillna(0, inplace=True)
  merged_df['Count_all'] = merged_df['Count_all'].apply(lambda x: int(x))
  merged_df['Count_specific'].fillna(0, inplace=True)
  merged_df['Risk_ratio'] = merged_df['Probability_specific'] / merged_df['Probability_all']
  merged_df['Probability_difference'] = merged_df['Probability_specific'] - merged_df['Probability_all']
  return merged_df

# Maak tabs voor sources
tb = widgets.TabBar(["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"])
results_dict = {}

for tab in tb.tab_names:

  results_dict[tab] = Calculate_metrics(third_level_df_dict[tab], third_level_df)
  with tb.output_to(tab, select=(0)):
    display(data_table.DataTable(results_dict[tab], include_index=False, num_rows_per_page=10))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Data voor 9 vacatures (uit dezelfde dataset als hierboven)

In [ ]:
vac_df_dict = {}

def custom_agg(series):
    return {
        'Count': series.count(),
        'Max_score': series.max(),
        'Avg_score': series.mean()
    }

for ISCO_code in ["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"]:
  tmp_results_df = pd.DataFrame({'Skill_id', 'Source', 'Count', 'Score'})
  data_df = pd.read_csv(f'/content/drive/MyDrive/Osso data/results/results per beroep/{ISCO_code}_results.csv')
  data_df = data_df.where(data_df['Vac_id'] == data_df['Vac_id'].unique()[1])
  total_skills_amt = len(data_df.index)
  # Group by 'Skill_id' and apply the custom aggregation function
  result = data_df.groupby(['Skill_id', 'Skill_text'])['Score'].agg(custom_agg).reset_index()

  # Use the map function to extract 'Count' and 'Max_Score' into separate columns
  result['Count'] = result['Score'].map(lambda x: x['Count'])
  result['Max_score'] = result['Score'].map(lambda x: x['Max_score'])
  result['Avg_score'] = result['Score'].map(lambda x: x['Avg_score'])
  result['Probability'] = result['Count'].map(lambda x: x / total_skills_amt)

  # Drop the original 'Score' column
  result.drop('Score', axis=1, inplace=True)

  vac_df_dict[ISCO_code] = result

In [ ]:
vac_third_level_df_dict = {}

# Haal third level skills op
third_level_skills = get_third_level_skills()

for ISCO_code in ["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"]:
  # Maak lege dictionary
  results_dict = {}

  # Itereer over algemene database
  for index, row in vac_df_dict[ISCO_code].iterrows():

    # Als de skills niet zelf een third level skill is
    if row['Skill_id'] not in third_level_skills:
      # Zoek third_level skills
      results = get_third_level_skill_from_uri(row['Skill_id'], third_level_skills)

      # Als er resultaten zijn voeg ze toe aan de dictionary
      if results:
        for result in results:
          results_dict = add_to_dict(result[0], row["Count"], "\n".join(part for part in result[1:] if part), results_dict)

    # Anders kunnen we hem direct toevoegen
    else:
      results_dict = add_to_dict(row["Skill_id"], row["Count"], row["Skill_text"], results_dict)

  # Tijdelijke lijst voor resultaten
  tmp_list = []

  # Maak resultaten interpreteerbaar voor Pandas DataFrame
  for item in results_dict.items():
    tmp_list.append({"Skill_id": item[0], "Text": item[1]["Text"], "Count": int(item[1]["Count"])})

  # Maak DataFrame
  vac_third_level_df_dict[ISCO_code] = pd.DataFrame(tmp_list)

  # Voeg probabilty toe
  total_amt = vac_third_level_df_dict[ISCO_code]["Count"].sum()
  vac_third_level_df_dict[ISCO_code]["Probability"] = vac_third_level_df_dict[ISCO_code]["Count"] / total_amt

### Statistieken berekenen

In [ ]:
from google.colab import widgets
from google.colab import data_table

# Maak tabs voor sources
tb = widgets.TabBar(["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"])
results_dict = {}

for tab in tb.tab_names:

  results_dict[tab] = Calculate_metrics(vac_third_level_df_dict[tab], third_level_df)
  with tb.output_to(tab, select=(0)):
    display(data_table.DataTable(results_dict[tab], include_index=False, num_rows_per_page=10))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Gebruikte tekst ophalen

In [ ]:
from google.colab import widgets
from google.colab import data_table

def print_texts(ISCO_code):
  data_df = pd.read_csv(f'/content/drive/MyDrive/Osso data/results/results per beroep/{ISCO_code}_results.csv')
  data_df = data_df.where(data_df['Vac_id'] == data_df['Vac_id'].unique()[1])
  texts = data_df['Vac_text'].dropna().unique()
  for text in texts:
    print(text + '\n')


# Maak tabs voor sources
tb = widgets.TabBar(["1349", "2431", "3115", "4222", "5414", "6113", "7233", "8332", "9112"])

for tab in tb.tab_names:
  with tb.output_to(tab, select=(0)):
    print_texts(tab)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Aalten (+21km) • In Person

Varsseveld (+19km) • In Person Uitzendbureau Lichtenvoorde..

Interieurverzorger

Hoog-Keppel (+25km) • In Person Uitzendbureau Lichtenvoorde..

Interieurverzorger/Schoonmaker Borculo • Erick

Opslaan

Notitie toevoegen

Vacature verbergen

Junior/Medior/Senior

Vacatureomschrijving Voor onze opdrachtgever, een groothandel in drogisterij- en reformartikelen in Borculo, zijn wij per direct op zoek naar een enthousiaste Interieurverzorger/ Schoonmaker voor 20 tot 24 uur per week.

Je werkt samen met andere collegas op de afdeling Interieurverzorging. Met hen zorg je er samen voor dat ons pand schoon wordt en blijft. Je hebt bij onze opdrachtgever meer dan 400 collegas. Samen dragen wij bij aan het op tijd leveren van meer dan 70.000 drogisterij- en reformproducten, bij zowel bedrijven als consumenten die wij onze klanten mogen noemen. Waarom zij bij ons werken? Flexibele werktijden en een goede sfeer worden als meest voorname reden aangedragen. De rest moet je

<IPython.core.display.Javascript object>